In [1]:
import plotly.graph_objects as go

fig = go.Figure(go.Surface(
    contours = {
        "x": {"show": True, "start": 1.5, "end": 2, "size": 0.04, "color":"white"},
        "z": {"show": True, "start": 0.5, "end": 0.8, "size": 0.05}
    },
    x = [1,2,3,4,5],
    y = [1,2,3,4,5],
    z = [
        [0, 1, 0, 1, 0],
        [1, 0, 1, 0, 1],
        [0, 1, 0, 1, 0],
        [1, 0, 1, 0, 1],
        [0, 1, 0, 1, 0]
    ]))
fig.update_layout(
        scene = {
            "xaxis": {"nticks": 20},
            "zaxis": {"nticks": 4},
            'camera_eye': {"x": 0, "y": -1, "z": 0.5},
            "aspectratio": {"x": 1, "y": 1, "z": 0.2}
        })
fig.show()


In [2]:
import plotly.graph_objects as go

fig = go.Figure(go.Surface(
    contours = {
        "x": {"show": True, "start": 1.5, "end": 2, "size": 0.04, "color":"white"},
        "z": {"show": True, "start": 0.5, "end": 1.8, "size": 0.2}
    },
    x = [1,2,3,4,5],
    y = [1,2,3,4,5],
    z = [
        [0, 1, 0, 1, 0],
        [1, 0, 2, 0, 1],
        [0, 1, 0, 1, 0],
        [1, 0, 2, 0, 1],
        [0, 1, 0, 1, 0]
    ]))
fig.update_layout(
        scene = {
            "xaxis": {"nticks": 20},
            "zaxis": {"nticks": 4},
            'camera_eye': {"x": 0, "y": -1, "z": 0.5},
            "aspectratio": {"x": 1, "y": 1, "z": 0.2}
        })
fig.show()


In [3]:
import plotly.graph_objects as go
import psycopg2

# open database connection
db_nn = psycopg2.connect(host = "localhost", dbname="Chemistry", user="postgres", password="postgres")


# generate random floating point values
from random import seed
from random import random
# seed random number generator
seed()

# Import math Library
import math

# Print the value of pi
# print (math.pi) 

plot_m = 20
plot_s = .1
m = int(plot_m/plot_s)
x = []
y = []
z = []

# x = [1,2,3,4,5]
# y = [1,2,3,4,5]
for i in range(0, m):
    j = i*plot_s
    x.append(j)
    y.append(j)
    
# print(x, y)

# create a cursor
cur = db_nn.cursor()
cur.execute('SELECT * FROM public."Neurons_2D" WHERE "Network" = 1')
nn_list = cur.fetchall()
# print(nn_list)

lnn = len(nn_list)


## Gaussian kernel generation to fill the z matrix.
# sigma = [1.0, 2.0, .5, .75, .25, 3, 2, 1.5]
# mux = [9, 3,15,18, 6, 2,14,7]
# muy = [9, 3, 4, 2,15,13, 7,3]
# amp = [1.0, 2, 1, 2,.3,10,15,6]

sigma = []
mux = []
muy = []
amp = []

for i in nn_list:
    # print(i)
    mux.append(i[0])
    muy.append(i[1])
    sigma.append(i[2])
    amp.append(i[3])
    
print('X     : ',mux)
print('Y     : ',muy)
print('sigma : ',sigma)
print('Ampli : ',amp)

la = len(amp)
# lx = length(x)
# ly = length(y)
mx = plot_m
my = plot_m
pi = math.pi
bmax = 0

# print(la) 

#for (k in 1:la)
#{
for j in range(0, m):
    a = []
    for i in range(0,m):
        b = 0
        for k in range(0, la):
            
            xi = x[i]
            if (mux[k]-x[i]>=mx/2):
                xi=x[i]+mx
            if (x[i]-mux[k]>=mx/2):
                xi=x[i]-mx
                
            yj = y[j]
            if (muy[k]-y[j]>=my/2):
                yj=y[j]+my
            if (y[j]-muy[k]>=my/2):
                yj=y[j]-my
        
            b = amp[k] * (1/(2*pi*pow(sigma[k],2))) * math.exp( -(pow((xi-mux[k]),2) + pow((yj-muy[k]),2))/(2*pow(sigma[k],2))) + b    
        ## z[i,j] = A[[k]] * exp( -((x[i]-mux[[k]])^2 + (y[j]-muy[[k]])^2)/(2*sigma[[k]]^2)) + z[i,j]
        
        bmax = max(b, bmax)
        a.append(b)
    z.append(a)
#    }
#  }

for i in range(0,m):
    a = []
    for j in range(0,m):
        v = 3*random()
        a.append(v)
        
    z.append(a)
    
# print(z)


# z = [
#        [0, 1, 0, 1, 0],
#        [1, 0, 2, 0, 1],
#        [0, 1, 0, 1, 0],
#        [1, 0, 2, 0, 1],
#        [0, 1, 0, 1, 0]
#    ]

fig = go.Figure(go.Surface(cmin = 0, cmax = bmax,
    contours = {
        # "x": {"show": True, "start": 1.5, "end": 2, "size": 0.04, "color":"white"},
        "z": {"show": True, "start": 0.1, "end": bmax, "size": 0.1}
    },
    x = x, y = y, z = z))
fig.update_layout(
        scene = {
            "xaxis": {"nticks": 20},
            "zaxis": {"nticks": 4},
            'camera_eye': {"x": 0, "y": -1, "z": 0.5},
            "aspectratio": {"x": 1, "y": 1, "z": 0.5}
        })
fig.show()

X     :  [1.0, 5.0, 9.0, 3.0, 15.0, 18.0, 6.0, 2.0, 14.0, 7.0, 14.0, 16.0, 15.0, 6.0]
Y     :  [1.0, 4.0, 9.0, 3.0, 4.0, 2.0, 15.0, 13.0, 7.0, 3.0, 14.0, 10.0, 11.0, 15.0]
sigma :  [1.0, 2.0, 1.0, 2.0, 0.5, 0.75, 0.25, 3.0, 2.0, 1.5, 2.0, 3.0, 1.0, 2.0]
Ampli :  [1.0, 4.0, 1.0, 2.0, 1.0, 2.0, 0.3, 10.0, 15.0, 6.0, 12.0, 17.0, 7.0, 3.0]


In [25]:
# print(nn_list)

a = 0

for i in nn_list:
    a = a+1    
    #print(a,i)
    
    l = []
    for j in range(0,len(i)):
        # print(j, i[j])
        l.append(i[j])
        
    # print(a,l)
    l[6] = a
    #print(a,l)
    sql = 'UPDATE public."Neurons_2D" SET "Neuron_ID" = '+str(l[6])+' WHERE "X" = '+str(l[0])+' AND "Y" = '+str(l[1])+' AND "Sigma" = '+str(l[2])+';'
    print(sql)

UPDATE public."Neurons_2D" SET "Neuron_ID" = 1 WHERE "X" = 1.0 AND "Y" = 1.0 AND "Sigma" = 1.0;
UPDATE public."Neurons_2D" SET "Neuron_ID" = 2 WHERE "X" = 5.0 AND "Y" = 4.0 AND "Sigma" = 2.0;
UPDATE public."Neurons_2D" SET "Neuron_ID" = 3 WHERE "X" = 9.0 AND "Y" = 9.0 AND "Sigma" = 1.0;
UPDATE public."Neurons_2D" SET "Neuron_ID" = 4 WHERE "X" = 3.0 AND "Y" = 3.0 AND "Sigma" = 2.0;
UPDATE public."Neurons_2D" SET "Neuron_ID" = 5 WHERE "X" = 15.0 AND "Y" = 4.0 AND "Sigma" = 0.5;
UPDATE public."Neurons_2D" SET "Neuron_ID" = 6 WHERE "X" = 18.0 AND "Y" = 2.0 AND "Sigma" = 0.75;
UPDATE public."Neurons_2D" SET "Neuron_ID" = 7 WHERE "X" = 6.0 AND "Y" = 15.0 AND "Sigma" = 0.25;
UPDATE public."Neurons_2D" SET "Neuron_ID" = 8 WHERE "X" = 2.0 AND "Y" = 13.0 AND "Sigma" = 3.0;
UPDATE public."Neurons_2D" SET "Neuron_ID" = 9 WHERE "X" = 14.0 AND "Y" = 7.0 AND "Sigma" = 2.0;
UPDATE public."Neurons_2D" SET "Neuron_ID" = 10 WHERE "X" = 7.0 AND "Y" = 3.0 AND "Sigma" = 1.5;
UPDATE public."Neurons_2D" SET "